# പ്രൊഡക്ഷനിൽ AutoGen ഏജന്റുകൾ: നിരീക്ഷണവും മൂല്യനിർണയവും

ഈ ട്യൂട്ടോറിയലിൽ, **[Autogen ഏജന്റുകളുടെ](https://github.com/microsoft/autogen) ആന്തരിക ഘട്ടങ്ങൾ (ട്രേസുകൾ) നിരീക്ഷിക്കുന്നതും** [Langfuse](https://langfuse.com) ഉപയോഗിച്ച് **അവയുടെ പ്രകടനം വിലയിരുത്തുന്നതും** എങ്ങനെ ചെയ്യാമെന്ന് പഠിക്കാം.

ഈ ഗൈഡ് **ഓൺലൈൻ**യും **ഓഫ്‌ലൈൻ**യും ഉപയോഗിക്കുന്ന മൂല്യനിർണയ മാനദണ്ഡങ്ങളെക്കുറിച്ചാണ്, ഏജന്റുകളെ വേഗത്തിലും വിശ്വസനീയമായും പ്രൊഡക്ഷനിലേക്ക് കൊണ്ടുവരാൻ ടീമുകൾ ഉപയോഗിക്കുന്നത്.

**എന്തുകൊണ്ട് AI ഏജന്റ് മൂല്യനിർണയം പ്രധാനമാണ്:**
- ടാസ്കുകൾ പരാജയപ്പെടുമ്പോഴും അപര്യാപ്തമായ ഫലങ്ങൾ നൽകുമ്പോഴും പ്രശ്നങ്ങൾ ഡീബഗ് ചെയ്യുക
- റിയൽ-ടൈമിൽ ചെലവും പ്രകടനവും നിരീക്ഷിക്കുക
- തുടർച്ചയായ ഫീഡ്ബാക്ക് വഴി വിശ്വസനീയതയും സുരക്ഷയും മെച്ചപ്പെടുത്തുക


## ഘട്ടം 1: പരിസ്ഥിതി വേരിയബിളുകൾ സജ്ജമാക്കുക

[Langfuse Cloud](https://cloud.langfuse.com/) ഉപയോഗിച്ച് സൈൻ അപ്പ് ചെയ്യുകയോ [സ്വയം ഹോസ്റ്റിംഗ് Langfuse](https://langfuse.com/self-hosting) ഉപയോഗിച്ച് Langfuse API കീകൾ നേടുക.

_**ശ്രദ്ധിക്കുക:** സ്വയം ഹോസ്റ്റിംഗ് ചെയ്യുന്നവർക്ക് [Terraform മോഡ്യൂളുകൾ](https://langfuse.com/self-hosting/azure) ഉപയോഗിച്ച് Azure-ൽ Langfuse ഡിപ്ലോയ് ചെയ്യാം. അല്ലെങ്കിൽ, [Helm ചാർട്ട്](https://langfuse.com/self-hosting/kubernetes-helm) ഉപയോഗിച്ച് Kubernetes-ൽ Langfuse ഡിപ്ലോയ് ചെയ്യാം._


In [5]:
import os

# Get keys for your project from the project settings page: https://cloud.langfuse.com
os.environ["LANGFUSE_PUBLIC_KEY"] = "pk-lf-..." 
os.environ["LANGFUSE_SECRET_KEY"] = "sk-lf-..." 
os.environ["LANGFUSE_HOST"] = "https://cloud.langfuse.com" # 🇪🇺 EU region
# os.environ["LANGFUSE_HOST"] = "https://us.cloud.langfuse.com" # 🇺🇸 US region

In [1]:
!pip install langfuse openlit


[notice] A new release of pip is available: 25.1.1 -> 25.2
[notice] To update, run: pip install --upgrade pip


പരിസ്ഥിതി വേരിയബിളുകൾ സജ്ജമാക്കിയ ശേഷം, നാം ഇപ്പോൾ Langfuse ക്ലയന്റ് ആരംഭിക്കാം. `get_client()` പരിസ്ഥിതി വേരിയബിളുകളിൽ നൽകിയിരിക്കുന്ന ക്രെഡൻഷ്യലുകൾ ഉപയോഗിച്ച് Langfuse ക്ലയന്റ് ആരംഭിക്കുന്നു.


In [6]:
from langfuse import Langfuse
 
# Filter out Autogen OpenTelemetryspans
langfuse = Langfuse(
    blocked_instrumentation_scopes=["autogen SingleThreadedAgentRuntime"]
)
 
# Verify connection
if langfuse.auth_check():
    print("Langfuse client is authenticated and ready!")
else:
    print("Authentication failed. Please check your credentials and host.")

Langfuse client is authenticated and ready!


## ഘട്ടം 2: OpenLit ഇൻസ്ട്രുമെന്റേഷൻ ആരംഭിക്കുക

ഇപ്പോൾ, [OpenLit](https://github.com/openlit/openlit) ഇൻസ്ട്രുമെന്റേഷൻ ആരംഭിക്കുന്നു. OpenLit സ്വയമേവ AutoGen പ്രവർത്തനങ്ങൾ പിടികൂടുകയും OpenTelemetry (OTel) സ്പാനുകൾ Langfuse-ലേക്ക് എക്സ്പോർട്ട് ചെയ്യുകയും ചെയ്യുന്നു.


In [7]:
import openlit
 
# Initialize OpenLIT instrumentation. The disable_batch flag is set to true to process traces immediately.
openlit.init(tracer=langfuse._otel_tracer, disable_batch=True, disabled_instrumentors=["mistral"])

## ഘട്ടം 3: നിങ്ങളുടെ ഏജന്റ് പ്രവർത്തിപ്പിക്കുക

ഇപ്പോൾ ഞങ്ങൾ നമ്മുടെ ഉപകരണങ്ങൾ പരീക്ഷിക്കാൻ ഒരു മൾട്ടി ടേൺ ഏജന്റ് സജ്ജമാക്കുന്നു.


In [2]:
import os

from autogen_agentchat.agents import AssistantAgent
from autogen_ext.models.azure import AzureAIChatCompletionClient
from azure.core.credentials import AzureKeyCredential
from autogen_agentchat.base import TaskResult

from autogen_agentchat.conditions import TextMentionTermination
from autogen_agentchat.teams import RoundRobinGroupChat

In [3]:
client = AzureAIChatCompletionClient(
    model="gpt-4o-mini",
    endpoint="https://models.inference.ai.azure.com",
    # To authenticate with the model you will need to generate a personal access token (PAT) in your GitHub settings.
    # Create your PAT token by following instructions here: https://docs.github.com/en/authentication/keeping-your-account-and-data-secure/managing-your-personal-access-tokens
    credential=AzureKeyCredential(os.environ["GITHUB_TOKEN"]),
    model_info={
        "json_output": True,
        "function_calling": True,
        "vision": True,
        "family": "unknown",
        "structured_output": False
    },
)

In [8]:
# 🍴 Agent 1 – proposes ONE healthy meal idea each turn
meal_planner_agent = AssistantAgent(
    "meal_planner_agent",
    model_client=client,
    description="A seasoned meal-planning coach who suggests balanced meals.",
    system_message="""
    You are a Meal-Planning Assistant with a decade of experience helping busy people prepare meals.
    Goal: propose the single best meal (breakfast, lunch, or dinner) given the user's context.
    Each response must contain ONLY one complete meal idea (title + very brief component list) — no extras.
    Keep it concise: skip greetings, chit-chat, and filler.
    """,
)

# 🥗 Agent 2 – checks nutritional quality & variety
nutritionist_agent = AssistantAgent(
    "nutritionist_agent",
    model_client=client,
    description="A registered dietitian ensuring meals meet nutritional standards.",
    system_message="""
    You are a Nutritionist focused on whole-food, macro-balanced eating.
    Evaluate the meal_planner_agent’s recommendation.
    If the meal is nutritionally sound, sufficiently varied, and portion-appropriate, respond with 'APPROVE'.
    Otherwise, give high-level guidance on how to improve it (e.g. 'add a plant-based protein') — do NOT provide a full alternative recipe.
    """,
)

In [9]:
# ✅ Chat stops once the nutritionist says APPROVE
termination = TextMentionTermination("APPROVE")

# 🔄 Alternate turns between the two agents until termination
team = RoundRobinGroupChat(
    [meal_planner_agent, nutritionist_agent],
    termination_condition=termination,
)

# Example kickoff
user_input = "I'm looking for a quick, delicious dinner I can prep after work. I have 30 minutes and minimal clean-up is ideal."

In [ ]:
with langfuse.start_as_current_span(name="create_meal_plan") as span:
    async for message in team.run_stream(task=user_input):
        if isinstance(message, TaskResult):
            print("Stop Reason:", message.stop_reason)
        else:
            print(message)

    span.update_trace(
        input=user_input,
        output=message.stop_reason,
    )

# Flush the trace to Langfuse for short-lived environments such as Jupyter Notebooks
langfuse.flush()

### ട്രേസ് ഘടന

Langfuse ഒരു **ട്രേസ്** രേഖപ്പെടുത്തുന്നു, ഇതിൽ **സ്പാനുകൾ** അടങ്ങിയിരിക്കുന്നു, അവ നിങ്ങളുടെ ഏജന്റിന്റെ ലജിക് ഓരോ ഘട്ടവും പ്രതിനിധീകരിക്കുന്നു. ഇവിടെ, ട്രേസ് ആകെ ഏജന്റ് പ്രവർത്തനവും താഴെപ്പറയുന്ന ഉപ-സ്പാനുകളും ഉൾക്കൊള്ളുന്നു:
- മീൽ പ്ലാനർ ഏജന്റ്
- പോഷക വിദഗ്ധർ (ന്യൂട്രിഷനിസ്റ്റ്) ഏജന്റുകൾ

ഇവ പരിശോധിച്ച് സമയം എവിടെ ചെലവാക്കുന്നു, എത്ര ടോക്കണുകൾ ഉപയോഗിക്കുന്നു തുടങ്ങിയവ കൃത്യമായി കാണാൻ കഴിയും:

![Langfuse-ലെ ട്രേസ് ട്രീ](https://langfuse.com/images/cookbook/example-autogen-evaluation/trace-tree.png)

_[ട്രേസിലേക്ക് ലിങ്ക്](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64)_  


## ഓൺലൈൻ മൂല്യനിർണ്ണയം

ഓൺലൈൻ മൂല്യനിർണ്ണയം എന്നത് ഏജന്റിനെ തത്സമയ, യഥാർത്ഥ ലോക സാഹചര്യത്തിൽ, അതായത് പ്രൊഡക്ഷനിൽ യഥാർത്ഥ ഉപയോഗത്തിനിടെ വിലയിരുത്തുന്നതാണ്. ഇത് യഥാർത്ഥ ഉപയോക്തൃ ഇടപെടലുകളിൽ ഏജന്റിന്റെ പ്രകടനം നിരീക്ഷിക്കുകയും ഫലങ്ങൾ തുടർച്ചയായി വിശകലനം ചെയ്യുകയും ചെയ്യുന്നതിൽ ഉൾപ്പെടുന്നു.

### പ്രൊഡക്ഷനിൽ നിരീക്ഷിക്കേണ്ട സാധാരണ മാനദണ്ഡങ്ങൾ

1. **ചെലവുകൾ** — ഇൻസ്ട്രുമെന്റേഷൻ ടോക്കൺ ഉപയോഗം പകർത്തുന്നു, ഇത് ഓരോ ടോക്കണിനും ഒരു വില നിശ്ചയിച്ച് ഏകദേശ ചെലവുകളായി മാറ്റാം.  
2. **ലാറ്റൻസി** — ഓരോ ഘട്ടം പൂർത്തിയാക്കാൻ എടുക്കുന്ന സമയം, അല്ലെങ്കിൽ മുഴുവൻ പ്രവർത്തനത്തിനുള്ള സമയം നിരീക്ഷിക്കുക.  
3. **ഉപയോക്തൃ പ്രതികരണം** — ഉപയോക്താക്കൾ നേരിട്ടുള്ള പ്രതികരണം (തമ്പ്‌സ് അപ്പ്/ഡൗൺ) നൽകാൻ കഴിയും, ഇത് ഏജന്റിനെ മെച്ചപ്പെടുത്താനും ശരിയാക്കാനും സഹായിക്കും.  
4. **LLM-നെ ജഡ്ജായി ഉപയോഗിക്കുക** — നിങ്ങളുടെ ഏജന്റിന്റെ ഔട്ട്പുട്ട് തത്സമയത്തിന് അടുത്ത് വിലയിരുത്താൻ ഒരു വേറിട്ട LLM ഉപയോഗിക്കുക (ഉദാ: വിഷമോ ശരിതോ എന്ന് പരിശോധിക്കുക).  

താഴെ, ഈ മാനദണ്ഡങ്ങളുടെ ഉദാഹരണങ്ങൾ കാണിക്കുന്നു.  


#### 1. ചെലവുകൾ

താഴെ `gpt-4o-mini` കോൾസിന്റെ ഉപയോഗം കാണിക്കുന്ന ഒരു സ്ക്രീൻഷോട്ട് നൽകിയിരിക്കുന്നു. ചെലവേറിയ ഘട്ടങ്ങൾ കണ്ടെത്താനും നിങ്ങളുടെ ഏജന്റിനെ മെച്ചപ്പെടുത്താനും ഇത് ഉപകാരപ്പെടും.

![ചെലവുകൾ](https://langfuse.com/images/cookbook/example-autogen-evaluation/gpt-4o-costs.png) 

_[ട്രേസ് ലിങ്ക്](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64)_


#### 2. ലാറ്റൻസി

ഓരോ ഘട്ടം പൂർത്തിയാക്കാൻ എത്ര സമയം എടുത്തുവെന്ന് നമുക്ക് കാണാനാകും. താഴെ കാണുന്ന ഉദാഹരണത്തിൽ, മുഴുവൻ പ്രവർത്തനത്തിനും ഏകദേശം 3 സെക്കൻഡ് എടുത്തു, ഇത് ഓരോ ഘട്ടത്തിലും വിഭജിച്ച് കാണാം. ഇത് ബോട്ടിൽനെക്കുകൾ കണ്ടെത്താനും നിങ്ങളുടെ ഏജന്റിനെ മെച്ചപ്പെടുത്താനും സഹായിക്കുന്നു.

![ലാറ്റൻസി](https://langfuse.com/images/cookbook/example-autogen-evaluation/agent-latency.png) 

_[ട്രേസ് ലിങ്ക്](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64?display=timeline)_


#### 3. ഉപയോക്തൃ പ്രതികരണം

നിങ്ങളുടെ ഏജന്റ് ഒരു ഉപയോക്തൃ ഇന്റർഫേസിൽ ഉൾപ്പെടുത്തിയിട്ടുണ്ടെങ്കിൽ, നേരിട്ടുള്ള ഉപയോക്തൃ പ്രതികരണം (ചാറ്റ് UIയിൽ ഒരു തമ്പ്‌സ്-അപ്പ്/ഡൗൺ പോലുള്ളത്) രേഖപ്പെടുത്താം.


In [10]:
from langfuse import get_client
 
langfuse = get_client()
 
# Option 1: Use the yielded span object from the context manager
with langfuse.start_as_current_span(
    name="autogen-request-user-feedback-1") as span:
    
    async for message in team.run_stream(task="Create a meal with potatoes"):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message)    
 
    # Score using the span object
    span.score_trace(
        name="user-feedback",
        value=1,
        data_type="NUMERIC",
        comment="This was delicious, thank you"
    )
 
# Option 2: Use langfuse.score_current_trace() if still in context
with langfuse.start_as_current_span(name="autogen-request-user-feedback-2") as span:
    # ... Autogen execution ...

    async for message in team.run_stream(task="I am allergic to gluten."):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message)    
 
    # Score using current context
    langfuse.score_current_trace(
        name="user-feedback",
        value=1,
        data_type="NUMERIC"
    )

id='da068880-22ae-4f01-9f01-2bb231939089' source='user' models_usage=None metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 43, 732669, tzinfo=datetime.timezone.utc) content='Create a meal with potatoes' type='TextMessage'
id='ad937ce4-3534-493f-824b-ca9c226b5287' source='meal_planner_agent' models_usage=RequestUsage(prompt_tokens=95, completion_tokens=30) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 45, 186423, tzinfo=datetime.timezone.utc) content='Potato and Spinach Frittata  \n- Eggs  \n- Potatoes  \n- Fresh spinach  \n- Onion  \n- Cheese (optional)  ' type='TextMessage'
id='50fd33c1-057f-49fe-afad-ee86d164296d' source='nutritionist_agent' models_usage=RequestUsage(prompt_tokens=132, completion_tokens=4) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 45, 581059, tzinfo=datetime.timezone.utc) content='APPROVE' type='TextMessage'
Stop Reason: Text 'APPROVE' mentioned
id='e371de6c-e5fc-42c1-8eda-e5b8cd5accab' source='user' models_usage=None met

In [ ]:
# Option 3: Use create_score() with trace ID (when outside context)
langfuse.create_score(
    trace_id="predefined_trace_id",
    name="user-feedback",
    value=1,
    data_type="NUMERIC",
    comment="This was correct, thank you"
)

ഉപയോക്തൃ പ്രതികരണം പിന്നീട് Langfuse-ൽ പകർത്തുന്നു:

![ഉപയോക്തൃ പ്രതികരണം Langfuse-ൽ പകർത്തുന്നു](https://langfuse.com/images/cookbook/example-autogen-evaluation/user-feedback.png)


#### 4. സ്വയം പ്രവർത്തിക്കുന്ന LLM-as-a-Judge സ്കോറിംഗ്

LLM-as-a-Judge നിങ്ങളുടെ ഏജന്റിന്റെ ഔട്ട്പുട്ട് സ്വയം വിലയിരുത്താനുള്ള മറ്റൊരു മാർഗമാണ്. ഔട്ട്പുട്ടിന്റെ ശരിതോറ്റം, വിഷമത, ശൈലി, അല്ലെങ്കിൽ നിങ്ങൾക്ക് പ്രാധാന്യമുള്ള മറ്റ് മാനദണ്ഡങ്ങൾ വിലയിരുത്താൻ ഒരു പ്രത്യേക LLM കോൾ സജ്ജമാക്കാം.

**പ്രവർത്തനരീതി**:
1. നിങ്ങൾ ഒരു **മൂല്യനിർണ്ണയ ടെംപ്ലേറ്റ്** നിർവചിക്കുന്നു, ഉദാ., "ടെക്സ്റ്റ് വിഷമകരമാണോ എന്ന് പരിശോധിക്കുക."
2. നിങ്ങൾ ഒരു മോഡൽ സെറ്റ് ചെയ്യുന്നു, ഇത് ജഡ്ജ്-മോഡലായി പ്രവർത്തിക്കുന്നു; ഈ സാഹചര്യത്തിൽ `gpt-4o-mini` Azure വഴി ചോദിക്കുന്നു.
3. നിങ്ങളുടെ ഏജന്റ് ഔട്ട്പുട്ട് സൃഷ്ടിക്കുന്ന ഓരോ തവണയും, ആ ഔട്ട്പുട്ട് ടെംപ്ലേറ്റിനൊപ്പം "ജഡ്ജ്" LLM-ലേക്ക് അയയ്ക്കുന്നു.
4. ജഡ്ജ് LLM ഒരു റേറ്റിംഗ് അല്ലെങ്കിൽ ലേബൽ നൽകുന്നു, അത് നിങ്ങൾ നിങ്ങളുടെ ഓബ്സർവബിലിറ്റി ടൂളിൽ ലോഗ് ചെയ്യുന്നു.

Langfuse-ൽ നിന്നുള്ള ഉദാഹരണം:

![LLM-as-a-Judge Evaluator](https://langfuse.com/images/cookbook/example-autogen-evaluation/evaluator.png)


In [12]:
with langfuse.start_as_current_span(name="autogen-request-user-feedback-2") as span:

    async for message in team.run_stream(task="I am a picky eater and not sure if you find something for me."):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message) 

    span.update_trace(
        input=user_input,
        output=message.stop_reason,
    )

langfuse.flush()

id='eefc628d-502f-451a-8f70-be486f62f8c5' source='user' models_usage=None metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 29, 171393, tzinfo=datetime.timezone.utc) content='I am a picky eater and not sure if you find something for me.' type='TextMessage'
id='13b3e14b-bcf7-42a5-80d6-54b0c7be765e' source='meal_planner_agent' models_usage=RequestUsage(prompt_tokens=352, completion_tokens=27) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 30, 433516, tzinfo=datetime.timezone.utc) content='Chicken Alfredo Pasta  \n- Gluten-free pasta  \n- Grilled chicken breast  \n- Heavy cream  \n- Parmesan cheese  \n- Garlic  ' type='TextMessage'
id='550f2dee-0e08-4bbd-b67f-991b467328f1' source='nutritionist_agent' models_usage=RequestUsage(prompt_tokens=386, completion_tokens=17) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 31, 505173, tzinfo=datetime.timezone.utc) content='Consider incorporating some vegetables, like spinach or broccoli, to increase the nutrien

ഈ ഉദാഹരണത്തിന്റെ ഉത്തരം "വിഷമമല്ല" എന്ന് വിലയിരുത്തിയിരിക്കുന്നതായി നിങ്ങൾക്ക് കാണാം.

![LLM-as-a-Judge മൂല്യനിർണയ സ്കോർ](https://langfuse.com/images/cookbook/example-autogen-evaluation/llm-as-a-judge-score.png)


#### 5. നിരീക്ഷണ മെട്രിക്‌സുകളുടെ അവലോകനം

ഈ മെട്രിക്‌സുകൾ എല്ലാം ഡാഷ്ബോർഡുകളിൽ ഒരുമിച്ച് ദൃശ്യമാക്കാൻ കഴിയും. ഇത് നിരവധി സെഷനുകളിൽ നിങ്ങളുടെ ഏജന്റിന്റെ പ്രകടനം എങ്ങനെ ഉള്ളുവെന്ന് വേഗത്തിൽ കാണാൻ നിങ്ങളെ സഹായിക്കുകയും ഗുണനിലവാര മെട്രിക്‌സുകൾ സമയത്തിനൊപ്പം ട്രാക്ക് ചെയ്യാൻ സഹായിക്കുകയും ചെയ്യുന്നു.

![നിരീക്ഷണ മെട്രിക്‌സുകളുടെ അവലോകനം](https://langfuse.com/images/cookbook/example-autogen-evaluation/dashboard.png)


## ഓഫ്‌ലൈൻ മൂല്യനിർണ്ണയം

ഓൺലൈൻ മൂല്യനിർണ്ണയം തത്സമയ പ്രതികരണത്തിനായി അനിവാര്യമാണ്, പക്ഷേ നിങ്ങൾക്ക് **ഓഫ്‌ലൈൻ മൂല്യനിർണ്ണയം** കൂടി ആവശ്യമുണ്ട്—വികസനത്തിനുമുമ്പോ അതിനിടെ systematic പരിശോധനകൾ. ഇത് മാറ്റങ്ങൾ പ്രൊഡക്ഷനിലേക്ക് കൊണ്ടുവരുന്നതിന് മുമ്പ് ഗുണനിലവാരവും വിശ്വാസ്യതയും നിലനിർത്താൻ സഹായിക്കുന്നു.


### ഡാറ്റാസെറ്റ് മൂല്യനിർണയം

ഓഫ്‌ലൈൻ മൂല്യനിർണയത്തിൽ, സാധാരണയായി നിങ്ങൾ:
1. ഒരു ബെഞ്ച്മാർക്ക് ഡാറ്റാസെറ്റ് (പ്രോംപ്റ്റ്, പ്രതീക്ഷിക്കുന്ന ഔട്ട്പുട്ട് ജോഡികളോടുകൂടിയ) ഉണ്ടാക്കുക
2. ആ ഡാറ്റാസെറ്റിൽ നിങ്ങളുടെ ഏജന്റ് പ്രവർത്തിപ്പിക്കുക
3. ഔട്ട്പുട്ടുകൾ പ്രതീക്ഷിക്കുന്ന ഫലങ്ങളുമായി താരതമ്യം ചെയ്യുക അല്ലെങ്കിൽ ഒരു അധിക സ്കോറിംഗ് മെക്കാനിസം ഉപയോഗിക്കുക

താഴെ, ചോദ്യങ്ങളും പ്രതീക്ഷിക്കുന്ന ഉത്തരങ്ങളും അടങ്ങിയ [q&a-dataset](https://huggingface.co/datasets/junzhang1207/search-dataset) ഉപയോഗിച്ച് ഈ സമീപനം നമുക്ക് പ്രദർശിപ്പിക്കുന്നു.


In [16]:
import pandas as pd
from datasets import load_dataset
 
# Fetch search-dataset from Hugging Face
dataset = load_dataset("junzhang1207/search-dataset", split = "train")
df = pd.DataFrame(dataset)
print("First few rows of search-dataset:")
print(df.head())

/Users/jannik/Documents/GitHub/ai-agents-for-beginners/.venv/lib/python3.13/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


First few rows of search-dataset:
                                     id  \
0  20caf138-0c81-4ef9-be60-fe919e0d68d4   
1  1f37d9fd-1bcc-4f79-b004-bc0e1e944033   
2  76173a7f-d645-4e3e-8e0d-cca139e00ebe   
3  5f5ef4ca-91fe-4610-a8a9-e15b12e3c803   
4  64dbed0d-d91b-4acd-9a9c-0a7aa83115ec   

                                            question  \
0                 steve jobs statue location budapst   
1  Why is the Battle of Stalingrad considered a t...   
2  In what year did 'The Birth of a Nation' surpa...   
3  How many Russian soldiers surrendered to AFU i...   
4   What event led to the creation of Google Images?   

                                     expected_answer       category       area  
0  The Steve Jobs statue is located in Budapest, ...           Arts  Knowledge  
1  The Battle of Stalingrad is considered a turni...   General News       News  
2  This question is based on a false premise. 'Th...  Entertainment       News  
3  About 300 Russian soldiers surrendered to t

അടുത്തതായി, റൺകളെ ട്രാക്ക് ചെയ്യുന്നതിനായി ലാംഗ്ഫ്യൂസിൽ ഒരു ഡാറ്റാസെറ്റ് എന്റിറ്റി സൃഷ്ടിക്കുന്നു. തുടർന്ന്, ഡാറ്റാസെറ്റിലെ ഓരോ ഇനവും സിസ്റ്റത്തിലേക്ക് ചേർക്കുന്നു.


In [17]:
from langfuse import Langfuse
langfuse = Langfuse()
 
langfuse_dataset_name = "qa-dataset_autogen-agent"
 
# Create a dataset in Langfuse
langfuse.create_dataset(
    name=langfuse_dataset_name,
    description="q&a dataset uploaded from Hugging Face",
    metadata={
        "date": "2025-03-21",
        "type": "benchmark"
    }
)

Dataset(id='cmcm7524d00kjad07s2cjwqcf', name='qa-dataset_autogen-agent', description='q&a dataset uploaded from Hugging Face', metadata={'date': '2025-03-21', 'type': 'benchmark'}, project_id='cloramnkj0002jz088vzn1ja4', created_at=datetime.datetime(2025, 7, 2, 16, 54, 7, 357000, tzinfo=datetime.timezone.utc), updated_at=datetime.datetime(2025, 7, 2, 16, 54, 7, 357000, tzinfo=datetime.timezone.utc))

In [18]:
df_25 = df.sample(25) # For this example, we upload only 25 dataset questions

for idx, row in df_25.iterrows():
    langfuse.create_dataset_item(
        dataset_name=langfuse_dataset_name,
        input={"text": row["question"]},
        expected_output={"text": row["expected_answer"]}
    )

![Dataset items in Langfuse](https://langfuse.com/images/cookbook/example-autogen-evaluation/example-dataset.png)


#### ഡാറ്റാസെറ്റിൽ ഏജന്റ് പ്രവർത്തിപ്പിക്കൽ

ആദ്യം, Azure OpenAI മോഡലുകൾ ഉപയോഗിച്ച് ചോദ്യങ്ങൾക്ക് ഉത്തരം നൽകുന്ന ഒരു ലളിതമായ Autogen ഏജന്റ് ഞങ്ങൾ തയ്യാറാക്കുന്നു.


In [8]:
import os
from dotenv import load_dotenv

from autogen_agentchat.agents import AssistantAgent
from autogen_core.models import UserMessage
from autogen_ext.models.azure import AzureAIChatCompletionClient
from azure.core.credentials import AzureKeyCredential
from autogen_core import CancellationToken
from autogen_agentchat.messages import TextMessage

In [ ]:
load_dotenv()
client = AzureAIChatCompletionClient(
    model="gpt-4o",
    endpoint="https://models.inference.ai.azure.com",
    # To authenticate with the model you will need to generate a personal access token (PAT) in your GitHub settings.
    # Create your PAT token by following instructions here: https://docs.github.com/en/authentication/keeping-your-account-and-data-secure/managing-your-personal-access-tokens
    credential=AzureKeyCredential(os.getenv("GITHUB_TOKEN")),
    max_tokens=5000,
    model_info={
        "json_output": True,
        "function_calling": False,
        "vision": False,
        "family": "unknown",
        "structured_output": True,
    },
)

result = await client.create([UserMessage(content="What is the capital of France?", source="user")])
print(result)

In [18]:
agent = AssistantAgent(
    name="assistant",
    model_client=client,
    tools=[],
    system_message="You are participant in a quizz show and you are given a question. You need to create a short answer to the question.",
)

അപ്പോൾ, നാം `my_agent()` എന്ന സഹായി ഫംഗ്ഷൻ നിർവചിക്കുന്നു.


In [19]:
async def my_agent(user_query: str):

    with langfuse.start_as_current_span(name="autogen-trace") as span:

        # Execute the agent response
        response = await agent.on_messages(
            [TextMessage(content=user_query, source="user")],
            cancellation_token=CancellationToken(),
        )

        span.update_trace(
            input=user_query,
            output=response.chat_message.content,
        )

    return str(response.chat_message.content)

# Test the function
await my_agent("What is the capital of France?")

'The capital of France is Paris.'

അവസാനമായി, ഓരോ ഡാറ്റാസെറ്റ് ഇനത്തിലും ലൂപ്പ് ചെയ്യുകയും, ഏജന്റിനെ പ്രവർത്തിപ്പിക്കുകയും, ട്രേസ് ഡാറ്റാസെറ്റ് ഇനത്തോട് ബന്ധിപ്പിക്കുകയും ചെയ്യുന്നു. ആവശ്യമെങ്കിൽ ഒരു ദ്രുത മൂല്യനിർണ്ണയ സ്കോർ ചേർക്കാനും കഴിയും.


In [20]:
dataset_name = "qa-dataset_autogen-agent"
current_run_name = "dev_tasks_run-autogen_gpt-4.1" # Identifies this specific evaluation run
current_run_metadata={"model_provider": "Azure", "model": "gpt-4.1"}
current_run_description="Evaluation run for Autogen model on July 3rd"

dataset = langfuse.get_dataset('qa-dataset_autogen-agent')

for item in dataset.items:
    print(f"Running evaluation for item: {item.id} (Input: {item.input})")
 
    # Use the item.run() context manager
    with item.run(
        run_name=current_run_name,
        run_metadata=current_run_metadata,
        run_description=current_run_description
    ) as root_span: 
        # All subsequent langfuse operations within this block are part of this trace.
        generated_answer = await my_agent(user_query = item.input["text"])
    
    print("Generated Answer: ", generated_answer)
 
print(f"\nFinished processing dataset '{dataset_name}' for run '{current_run_name}'.")

langfuse.flush()

Running evaluation for item: 09810cc4-9992-4712-a3b2-7224da31776a (Input: {'text': 'In Hindu mythology, which deity is the Ganges river dolphin associated with?'})
Generated Answer:  In Hindu mythology, the Ganges river dolphin is associated with the deity Ganga.
Running evaluation for item: bb113f94-7723-47c6-8c34-59d883044514 (Input: {'text': 'What significant discovery did the LHCb collaboration report in 2015?'})
Generated Answer:  In 2015, the LHCb collaboration reported the discovery of pentaquark particles.
Running evaluation for item: 4d8ae54e-ceab-46d0-ad2c-6e8e223589a9 (Input: {'text': 'What is the MÄ\x81ori name for the red-crowned parakeet?'})
Generated Answer:  The Māori name for the red-crowned parakeet is kākāriki.
Running evaluation for item: 21e5a0d5-f619-4a73-868e-9955053b3e72 (Input: {'text': 'Who starred in the 1978 television film adaptation of Les MisÃ©rables?'})
Generated Answer:  Richard Jordan starred as Jean Valjean in the 1978 television film adaptation of Le

നിങ്ങൾ ഈ പ്രക്രിയ വ്യത്യസ്ത ഏജന്റ് കോൺഫിഗറേഷനുകൾ ഉപയോഗിച്ച് ആവർത്തിക്കാം, ഉദാഹരണത്തിന്:  
- മോഡലുകൾ (gpt-4o-mini, gpt-4.1, മുതലായവ)  
- പ്രോംപ്റ്റുകൾ  
- ഉപകരണങ്ങൾ (തിരയൽ vs. തിരയൽ ഇല്ല)  
- ഏജന്റിന്റെ സങ്കീർണ്ണത (മൾട്ടി ഏജന്റ് vs. സിംഗിൾ ഏജന്റ്)  

അതിനുശേഷം അവ Langfuse-ൽ സൈഡ്-ബൈ-സൈഡ് താരതമ്യം ചെയ്യുക. ഈ ഉദാഹരണത്തിൽ, ഞാൻ 25 ഡാറ്റാസെറ്റ് ചോദ്യങ്ങളിൽ ഏജന്റിനെ 3 തവണ പ്രവർത്തിപ്പിച്ചു. ഓരോ റൺക്കും, ഞാൻ വ്യത്യസ്ത Azure OpenAI മോഡൽ ഉപയോഗിച്ചു. വലിയ മോഡൽ ഉപയോഗിക്കുമ്പോൾ ശരിയായി ഉത്തരം നൽകിയ ചോദ്യങ്ങളുടെ എണ്ണം മെച്ചപ്പെടുന്നതാണ് കാണുന്നത് (പ്രതീക്ഷിച്ചതുപോലെ). `correct_answer` സ്കോർ [LLM-as-a-Judge Evaluator](https://langfuse.com/docs/scores/model-based-evals) ഉപയോഗിച്ച് സൃഷ്ടിക്കപ്പെട്ടതാണ്, ഇത് ഡാറ്റാസെറ്റിൽ നൽകിയ സാമ്പിൾ ഉത്തരം അടിസ്ഥാനമാക്കി ചോദ്യത്തിന്റെ ശരിതെറ്റുകൾ വിലയിരുത്താൻ ക്രമീകരിച്ചിരിക്കുന്നു.  

![ഡാറ്റാസെറ്റ് റൺ അവലോകനം](https://langfuse.com/images/cookbook/example-autogen-evaluation/dataset_runs.png)  
![ഡാറ്റാസെറ്റ് റൺ താരതമ്യം](https://langfuse.com/images/cookbook/example-autogen-evaluation/dataset-run-comparison.png)  


---

<!-- CO-OP TRANSLATOR DISCLAIMER START -->
**അസത്യവാദം**:  
ഈ രേഖ AI വിവർത്തന സേവനമായ [Co-op Translator](https://github.com/Azure/co-op-translator) ഉപയോഗിച്ച് വിവർത്തനം ചെയ്തതാണ്. കൃത്യതയ്ക്കായി ഞങ്ങൾ ശ്രമിക്കുന്നുവെങ്കിലും, ഓട്ടോമേറ്റഡ് വിവർത്തനങ്ങളിൽ പിശകുകൾ അല്ലെങ്കിൽ തെറ്റായ വിവരങ്ങൾ ഉണ്ടാകാൻ സാധ്യതയുണ്ട്. അതിന്റെ സ്വാഭാവിക ഭാഷയിലുള്ള മൗലിക രേഖ പ്രാമാണികമായ ഉറവിടമായി പരിഗണിക്കണം. നിർണായകമായ വിവരങ്ങൾക്ക്, പ്രൊഫഷണൽ മനുഷ്യ വിവർത്തനം ശുപാർശ ചെയ്യുന്നു. ഈ വിവർത്തനം ഉപയോഗിക്കുന്നതിൽ നിന്നുണ്ടാകുന്ന തെറ്റിദ്ധാരണകൾക്കോ തെറ്റായ വ്യാഖ്യാനങ്ങൾക്കോ ഞങ്ങൾ ഉത്തരവാദികളല്ല.
<!-- CO-OP TRANSLATOR DISCLAIMER END -->
